In [2]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [4]:
#Extracting the text from the Book
def load_pdf_file(data):
    loader = DirectoryLoader(data, glob = "*.pdf",loader_cls=PyPDFLoader)

    documents = loader.load()

    return documents

In [6]:
extracted_data = load_pdf_file(data='../Medical-Chatbot/')

In [7]:
extracted_data

[Document(metadata={'producer': 'GPL Ghostscript 8.62', 'creator': 'UnknownApplication', 'creationdate': '2008-08-25T20:58:19+01:00', 'moddate': '2008-08-26T10:30:39+04:30', 'title': 'Untitled', 'source': '..\\Medical-Chatbot\\book.pdf', 'total_pages': 815, 'page': 0, 'page_label': '1'}, page_content=''),
 Document(metadata={'producer': 'GPL Ghostscript 8.62', 'creator': 'UnknownApplication', 'creationdate': '2008-08-25T20:58:19+01:00', 'moddate': '2008-08-26T10:30:39+04:30', 'title': 'Untitled', 'source': '..\\Medical-Chatbot\\book.pdf', 'total_pages': 815, 'page': 1, 'page_label': '2'}, page_content='The British\nMedical Association\nA-Z\nFA M I L Y\nMEDICAL\nENCYCLOPEDIA\nBMA CONSULTING MEDICAL EDITOR\nDr. Michael Peters'),
 Document(metadata={'producer': 'GPL Ghostscript 8.62', 'creator': 'UnknownApplication', 'creationdate': '2008-08-25T20:58:19+01:00', 'moddate': '2008-08-26T10:30:39+04:30', 'title': 'Untitled', 'source': '..\\Medical-Chatbot\\book.pdf', 'total_pages': 815, 'page

In [8]:
def text_split(extracted_data):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size = 500, chunk_overlap = 20)
    text_chunks = text_splitter.split_documents(extracted_data)
    return text_chunks

In [9]:
text_chunks = text_split(extracted_data=extracted_data)
print(len(text_chunks))

9105


In [10]:
#Embedding MODEL - 
from langchain.embeddings import HuggingFaceBgeEmbeddings
def download_hugging_face_model():
    embeddings = HuggingFaceBgeEmbeddings(model_name = 'sentence-transformers/all-MiniLM-L6-v2')
    return embeddings

In [13]:
embeddings = download_hugging_face_model()

C:\Users\mahob\AppData\Local\Temp\ipykernel_18044\1952567996.py:4: LangChainDeprecationWarning: The class `HuggingFaceBgeEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceBgeEmbeddings(model_name = 'sentence-transformers/all-MiniLM-L6-v2')


In [57]:
#Init Pinecone
from pinecone.grpc import PineconeGRPC as Pinecone
from pinecone import ServerlessSpec
from dotenv import load_dotenv
import os
from pinecone import Pinecone
load_dotenv()
PINECONE_API_KEY = os.environ.get('PINECONE_API_KEY')

pc = Pinecone(api_key = PINECONE_API_KEY)

pc = Pinecone(api_key=PINECONE_API_KEY)
index = pc.Index("medical-knowledge-base")

In [53]:
from langchain_pinecone import PineconeVectorStore
index_name = "medical-knowledge-base"
docsearch = PineconeVectorStore.from_documents(
    index_name=index_name,
    documents=text_chunks,
    embedding=embeddings
)

KeyboardInterrupt: 

In [54]:
retriever = docsearch.as_retriever(search_type = 'similarity', search_kwargs = {"k" : 3})

In [60]:
from langchain_openai import OpenAI
OPEN_AI_API_KEY = os.environ.get('OPENAI_API_KEY')
llm = OpenAI(temperature=0.4,max_tokens=500,api_key=OPEN_AI_API_KEY)



In [42]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [43]:
system_prompt = (
    "You are an assistant for question-answering task"
    "Use the following pieces of retrieved context to answer"
    "the question. If you don't know the answer, say that"
    "don't know the answer. User three sentences maximum and keep the answer concise"
    "{context}"
)

In [44]:
prompt = ChatPromptTemplate.from_messages(
    [
        ("system",system_prompt),
        ("human","{input}"),
    ]
)

In [61]:
question_answer_chain = create_stuff_documents_chain(llm,prompt)
rag_chain = create_retrieval_chain(retriever,question_answer_chain)

In [62]:
response = rag_chain.invoke({"input" : "What is dose in term of medicine?"})
print(response['answer'])



Dose is the amount of a medication or drug that is prescribed or administered to a patient. It can be measured in terms of weight, volume, or its effects on the body. In the case of radiotherapy, dose is also used to refer to the amount of radiation absorbed by the body during a session. The goal of determining a dose is to ensure that it is effective in treating the illness without causing harm to the patient.
